In [37]:
#!pip3 install pyspark
#!pip3 install tensorflow-recommenders
#!pip3 install -q scann

DEPRECATION: Configuring installation scheme with distutils config files is deprecated and will no longer work in the near future. If you are using a Homebrew or Linuxbrew Python, please see discussion at https://github.com/Homebrew/homebrew-core/issues/76621
ERROR: Could not find a version that satisfies the requirement scann (from versions: none)
ERROR: No matching distribution found for scann


In [1]:
# Python ≥3.5 is required
import sys
assert sys.version_info >= (3, 5)

# Scikit-Learn ≥0.20 is required
import sklearn
assert sklearn.__version__ >= "0.20"

try:
    # %tensorflow_version only exists in Colab.
    %tensorflow_version 2.x
except Exception:
    pass

# TensorFlow ≥2.0 is required
import tensorflow as tf
assert tf.__version__ >= "2.0"

# Common imports
import numpy as np
import os
import pandas as pd 
import tensorflow as tf
from tensorflow import keras
#import spark

# to make this notebook's output stable across runs
np.random.seed(42)

# To plot pretty figures
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
mpl.rc('axes', labelsize=14)
mpl.rc('xtick', labelsize=12)
mpl.rc('ytick', labelsize=12)

In [16]:
'''import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import SQLContext
from pyspark.sql import functions as F
from pyspark.sql import Window
from pyspark.sql.types import StructType,StructField, StringType, IntegerType, ArrayType, DoubleType, BooleanType

In [2]:
pd.set_option("display.max_rows", None, "display.max_columns", None)

In [18]:
#sc = SparkSession.builder.master("local").appName("Recommendation").getOrCreate()
#spark = SparkSession(sc)

In [3]:
#Pandas
articlesDF = pd.read_csv('articles.csv')
customersDF = pd.read_csv('customers.csv')
transactions_trainDF = pd.read_csv('transactions_train.csv')
'''
PySpark
articles = spark.read.option('header', True).csv('articles.csv')
customer = spark.read.option('header', True).csv('customers.csv')
transactions_train = spark.read.option('header', True).csv('transactions_train.csv')
'''

"\nPySpark\narticles = spark.read.option('header', True).csv('articles.csv')\ncustomer = spark.read.option('header', True).csv('customers.csv')\ntransactions_train = spark.read.option('header', True).csv('transactions_train.csv')\n"

In [6]:
articlesDF.shape , customersDF.shape, transactions_trainDF.shape

((105542, 25), (1371980, 7), (31788324, 5))

### Articles

In [8]:
articlesDF.head(4)

article_id  product_code          prod_name  product_type_no  \
0   108775015        108775          Strap top              253   
1   108775044        108775          Strap top              253   
2   108775051        108775      Strap top (1)              253   
3   110065001        110065  OP T-shirt (Idro)              306   

  product_type_name  product_group_name  graphical_appearance_no  \
0          Vest top  Garment Upper body                  1010016   
1          Vest top  Garment Upper body                  1010016   
2          Vest top  Garment Upper body                  1010017   
3               Bra           Underwear                  1010016   

  graphical_appearance_name  colour_group_code colour_group_name  \
0                     Solid                  9             Black   
1                     Solid                 10             White   
2                    Stripe                 11         Off White   
3                     Solid                  9             Black   

   perceived_colour_value_id perceived_colour_value_name  \
0                          4                        Dark   
1                          3                       Light   
2                          1                 Dusty Light   
3                          4                        Dark   

   perceived_colour_master_id perceived_colour_master_name  department_no  \
0                           5                        Black           1676   
1                           9                        White           1676   
2                           9                        White           1676   
3                           5                        Black           1339   

  department_name index_code        index_name  index_group_no  \
0    Jersey Basic          A        Ladieswear               1   
1    Jersey Basic          A        Ladieswear               1   
2    Jersey Basic          A        Ladieswear               1   
3  Clean Lingerie          B  Lingeries/Tights               1   

  index_group_name  section_no            section_name  garment_group_no  \
0       Ladieswear          16  Womens Everyday Basics              1002   
1       Ladieswear          16  Womens Everyday Basics              1002   
2       Ladieswear          16  Womens Everyday Basics              1002   
3       Ladieswear          61         Womens Lingerie              1017   

  garment_group_name                                        detail_desc  
0       Jersey Basic            Jersey top with narrow shoulder straps.  
1       Jersey Basic            Jersey top with narrow shoulder straps.  
2       Jersey Basic            Jersey top with narrow shoulder straps.  
3  Under-, Nightwear  Microfibre T-shirt bra with underwired, moulde...

In [9]:
articlesDF.isnull().sum()

article_id                        0
product_code                      0
prod_name                         0
product_type_no                   0
product_type_name                 0
product_group_name                0
graphical_appearance_no           0
graphical_appearance_name         0
colour_group_code                 0
colour_group_name                 0
perceived_colour_value_id         0
perceived_colour_value_name       0
perceived_colour_master_id        0
perceived_colour_master_name      0
department_no                     0
department_name                   0
index_code                        0
index_name                        0
index_group_no                    0
index_group_name                  0
section_no                        0
section_name                      0
garment_group_no                  0
garment_group_name                0
detail_desc                     416
dtype: int64

In [5]:
articlesDF = articlesDF.dropna()

In [11]:
articlesDF.isnull().sum()

article_id                      0
product_code                    0
prod_name                       0
product_type_no                 0
product_type_name               0
product_group_name              0
graphical_appearance_no         0
graphical_appearance_name       0
colour_group_code               0
colour_group_name               0
perceived_colour_value_id       0
perceived_colour_value_name     0
perceived_colour_master_id      0
perceived_colour_master_name    0
department_no                   0
department_name                 0
index_code                      0
index_name                      0
index_group_no                  0
index_group_name                0
section_no                      0
section_name                    0
garment_group_no                0
garment_group_name              0
detail_desc                     0
dtype: int64

In [12]:
articlesDF.columns

Index(['article_id', 'product_code', 'prod_name', 'product_type_no',
       'product_type_name', 'product_group_name', 'graphical_appearance_no',
       'graphical_appearance_name', 'colour_group_code', 'colour_group_name',
       'perceived_colour_value_id', 'perceived_colour_value_name',
       'perceived_colour_master_id', 'perceived_colour_master_name',
       'department_no', 'department_name', 'index_code', 'index_name',
       'index_group_no', 'index_group_name', 'section_no', 'section_name',
       'garment_group_no', 'garment_group_name', 'detail_desc'],
      dtype='object')

In [4]:
articlesDF = articlesDF[['article_id', 'product_code', 'prod_name', 'product_type_no','department_no', 'department_name', 'detail_desc']]
articlesDF.head(4)

article_id  product_code          prod_name  product_type_no  \
0   108775015        108775          Strap top              253   
1   108775044        108775          Strap top              253   
2   108775051        108775      Strap top (1)              253   
3   110065001        110065  OP T-shirt (Idro)              306   

   department_no department_name  \
0           1676    Jersey Basic   
1           1676    Jersey Basic   
2           1676    Jersey Basic   
3           1339  Clean Lingerie   

                                         detail_desc  
0            Jersey top with narrow shoulder straps.  
1            Jersey top with narrow shoulder straps.  
2            Jersey top with narrow shoulder straps.  
3  Microfibre T-shirt bra with underwired, moulde...

In [32]:
articlesDF.shape

(105126, 7)

### Transaction

In [7]:
transactions_trainDF['t_dat'].max() 

'2020-09-22'

In [25]:
transactions_trainDF = transactions_trainDF[transactions_trainDF['t_dat'] >= '2020-01-01']

In [26]:
transactions_trainDF.isnull().sum()

t_dat               0
customer_id         0
article_id          0
price               0
sales_channel_id    0
dtype: int64

In [27]:
transactions_trainDF.head(4)

t_dat                                        customer_id  \
20808192  2020-01-01  0034b3dced3e565a43438bdfb5447e7321fea65388b398...   
20808193  2020-01-01  00410b91d62eefa76958fa5cac12f5daa7cfc0556e417d...   
20808194  2020-01-01  00410b91d62eefa76958fa5cac12f5daa7cfc0556e417d...   
20808195  2020-01-01  004b0fb384bcab2f8e1059dd5ca68c17580365ab95c05a...   

          article_id     price  sales_channel_id  
20808192   835247001  0.033881                 2  
20808193   802930002  0.067780                 2  
20808194   760084008  0.025407                 2  
20808195   804662002  0.033881                 2

In [31]:
transactions_trainDF.shape

(10980132, 5)

### Customers

In [35]:
customersDF.head(4)

customer_id  FN  Active  \
0  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3... NaN     NaN   
1  0000423b00ade91418cceaf3b26c6af3dd342b51fd051e... NaN     NaN   
2  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca... NaN     NaN   
3  00005ca1c9ed5f5146b52ac8639a40ca9d57aeff4d1bd2... NaN     NaN   

  club_member_status fashion_news_frequency   age  \
0             ACTIVE                   NONE  49.0   
1             ACTIVE                   NONE  25.0   
2             ACTIVE                   NONE  24.0   
3             ACTIVE                   NONE  54.0   

                                         postal_code  
0  52043ee2162cf5aa7ee79974281641c6f11a68d276429a...  
1  2973abc54daa8a5f8ccfe9362140c63247c5eee03f1d93...  
2  64f17e6a330a85798e4998f62d0930d14db8db1c054af6...  
3  5d36574f52495e81f019b680c843c443bd343d5ca5b1c2...

In [34]:
#articlesDF.isnull().sum()

In [27]:
customersDF.isnull().sum()

customer_id                    0
FN                        895050
Active                    907576
club_member_status          6062
fashion_news_frequency     16009
age                        15861
postal_code                    0
dtype: int64

In [11]:
#customersDF = customersDF.dropna()

In [36]:
#customersDF.isnull().sum()

In [33]:
#transactions_trainDF.isnull().sum()

In [29]:
tmp = transactions_trainDF.groupby(['customer_id','article_id'])['t_dat'].agg('count').reset_index()
tmp.head()

customer_id  article_id  t_dat
0  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   176209023      1
1  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   568601006      2
2  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   568601043      1
3  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   607642008      1
4  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   625548001      1

### Merge Customer and Transactions to then clean the data based on Customer's transactions

In [5]:
customerTransactionsDF = pd.merge(transactions_trainDF, customersDF, on='customer_id', how='left', suffixes=('', '_remove'))
customerTransactionsDF.head(4)

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   
2  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   505221004   
3  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   685687003   

      price  sales_channel_id   FN  Active club_member_status  \
0  0.050831                 2  NaN     NaN             ACTIVE   
1  0.030492                 2  NaN     NaN             ACTIVE   
2  0.015237                 2  1.0     1.0             ACTIVE   
3  0.016932                 2  1.0     1.0             ACTIVE   

  fashion_news_frequency   age  \
0                   NONE  24.0   
1                   NONE  24.0   
2              Regularly  32.0   
3              Regularly  32.0   

                                         postal_code  
0  64f17e6a330a85798e4998f62d0930d14db8db1c054af6...  
1  64f17e6a330a85798e4998f62d0930d14db8db1c054af6...  
2  8d6f45050876d059c830a0fe63f1a4c022de279bb68ce3...  
3  8d6f45050876d059c830a0fe63f1a4c022de279bb68ce3...

In [15]:
customerTransactionsDF.shape

(31788324, 11)

In [16]:
customerTransactionsDF.isnull().sum()

t_dat                            0
customer_id                      0
article_id                       0
price                            0
sales_channel_id                 0
FN                        18209837
Active                    18412468
club_member_status           62165
fashion_news_frequency      141711
age                         140258
postal_code                      0
dtype: int64

In [48]:
customerTransactionsDF['FN'].value_counts()

1.0    4740096
Name: FN, dtype: int64

In [6]:
customerTransactionsDF = customerTransactionsDF.drop(['FN', 'club_member_status', 'sales_channel_id','fashion_news_frequency', 'postal_code'], axis=1)

In [18]:
customerTransactionsDF.head(3)

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   
2  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   505221004   

      price  sales_channel_id  Active   age  
0  0.050831                 2     NaN  24.0  
1  0.030492                 2     NaN  24.0  
2  0.015237                 2     1.0  32.0

In [62]:
customerTransactionsDF.isna().sum()

t_dat                     0
customer_id               0
article_id                0
price                     0
sales_channel_id          0
Active              6307671
age                   39698
dtype: int64

In [54]:
customerTransactionsDF['Active'].value_counts()

1.0    4672461
Name: Active, dtype: int64

In [19]:
customerTransactionsDF['Active'].fillna(value=0.0, inplace=True)

In [20]:
customerTransactionsDF.isnull().sum()

t_dat                    0
customer_id              0
article_id               0
price                    0
sales_channel_id         0
Active                   0
age                 140258
dtype: int64

In [65]:
customerTransactionsDF.head()

t_dat                                        customer_id  article_id  \
0  2020-01-01  0034b3dced3e565a43438bdfb5447e7321fea65388b398...   835247001   
1  2020-01-01  00410b91d62eefa76958fa5cac12f5daa7cfc0556e417d...   802930002   
2  2020-01-01  00410b91d62eefa76958fa5cac12f5daa7cfc0556e417d...   760084008   
3  2020-01-01  004b0fb384bcab2f8e1059dd5ca68c17580365ab95c05a...   804662002   
4  2020-01-01  004b0fb384bcab2f8e1059dd5ca68c17580365ab95c05a...   801554002   

      price  sales_channel_id  Active   age  
0  0.033881                 2     1.0  42.0  
1  0.067780                 2     0.0  53.0  
2  0.025407                 2     0.0  53.0  
3  0.033881                 2     0.0   NaN  
4  0.016932                 2     0.0   NaN

### Merge customerTransaction with article dataset

In [66]:
articlesDF.head(2)

article_id  product_code  prod_name  product_type_no  department_no  \
0   108775015        108775  Strap top              253           1676   
1   108775044        108775  Strap top              253           1676   

  department_name                              detail_desc  
0    Jersey Basic  Jersey top with narrow shoulder straps.  
1    Jersey Basic  Jersey top with narrow shoulder straps.

In [67]:
articlesDF.shape, customerTransactionsDF.shape

((105126, 7), (10980132, 7))

In [10]:
HMRecommendationDF = pd.merge(customerTransactionsDF, articlesDF, on='article_id', how='left', suffixes=('','_remove'))
HMRecommendationDF.head()

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   
2  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   505221004   
3  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   685687003   
4  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   685687004   

      price  Active   age  product_code                 prod_name  \
0  0.050831     NaN  24.0        663713  Atlanta Push Body Harlow   
1  0.030492     NaN  24.0        541518   Rae Push (Melbourne) 2p   
2  0.015237     1.0  32.0        505221               Inca Jumper   
3  0.016932     1.0  32.0        685687      W YODA KNIT OL OFFER   
4  0.016932     1.0  32.0        685687      W YODA KNIT OL OFFER   

   product_type_no  department_no      department_name  \
0              283           1338  Expressive Lingerie   
1              306           1334      Casual Lingerie   
2              252           5963     Tops Knitwear DS   
3              252           3090            Campaigns   
4              252           3090            Campaigns   

                                         detail_desc  
0  Lace push-up body with underwired, moulded, pa...  
1  Lace push-up bras with underwired, moulded, pa...  
2  Jumper in rib-knit cotton with hard-worn detai...  
3  V-neck knitted jumper with long sleeves and ri...  
4  V-neck knitted jumper with long sleeves and ri...

In [11]:
HMRecommendationDF.shape

(31788324, 17)

In [23]:
HMRecommendationDF.isnull().sum()

t_dat                    0
customer_id              0
article_id               0
price                    0
sales_channel_id         0
Active                   0
age                 140258
product_code        115027
prod_name           115027
product_type_no     115027
department_no       115027
department_name     115027
detail_desc         115027
dtype: int64

In [71]:
HMRecommendationDF[HMRecommendationDF['product_code'].isnull()]

t_dat                                        customer_id  \
946       2020-01-01  1647d17ab2a8120bf9cd4d94a330e6c8b640d326303c8d...   
2157      2020-01-01  2eafb706a8202fa2fb19e4128f841b9479605e30fc29ce...   
2490      2020-01-01  3622122f8ac9f48a8735826ebdafc874ebe835964a0e74...   
2639      2020-01-01  385865ada6e163a43474410c8a6476ac323027ec30986f...   
4035      2020-01-01  533980d496cde9b02c5cdfb654763c62330bf5a6ef81aa...   
5112      2020-01-01  6881b10bf7d5dfa456765858c3f686de0910fd23d7e967...   
9307      2020-01-01  ba7dab25880d90046b94a85f4da811bbae301a87b423a5...   
9326      2020-01-01  baf99419872b6f183f4846caffdadd19cae33b7397ed6f...   
9394      2020-01-01  bc29a4095be4798d09be705a787cc4b1edc58b48543c25...   
9679      2020-01-01  c337ff381aae83dd63aeaf8e585dae6f787b8cee3b5e95...   
10343     2020-01-01  d1c69d96a8d77746be41ad6407eb6d99c301e318d155be...   
10405     2020-01-01  d2bb6fb05d66e8a11256edb198c4c1dabee54b906096b8...   
12235     2020-01-01  f5dab969e4b980f9041346389d3108814c7e402ee8fe31...   
12648     2020-01-01  fe4db96a9d66222ce5e169e009536a78f7e8dae4fbc5e1...   
13698     2020-01-02  057dddf8b97b949ae81c5e6f1269027ce573fca569b9c2...   
13729     2020-01-02  05d6a73a0efc6e9b6fc4d319bd050f0a3fa5a1339e08d4...   
13730     2020-01-02  05d6a73a0efc6e9b6fc4d319bd050f0a3fa5a1339e08d4...   
15126     2020-01-02  0e3c63e0dc73b54f955220f0d0fc0773edfb29e6fe311a...   
15979     2020-01-02  12de31f9ef479795493a2b3a97cd2a4bd7f8a42d6e964a...   
16427     2020-01-02  153ccc0df7eeb43d99c165d9b290d25c085885d3e645a2...   
18430     2020-01-02  20677eba17034f64bcfd360dc9eb94da137522179a2530...   
19961     2020-01-02  28e06c4ca47dc83f82e600129249d3b6dff17966f0f052...   
20406     2020-01-02  2bd6c729a1f8ce7a74ec5a26c6537d0ba9c15d2c4d3101...   
21056     2020-01-02  2f0ae540e21c49406240c9556f0741f34198b3de1de61f...   
21566     2020-01-02  323fcde101339be3d77682099ccd3fa471eb479cefbffa...   
21990     2020-01-02  3454e4d07d17c4698b6190a0ac54266c9d9dd75e933127...   
21997     2020-01-02  3454e4d07d17c4698b6190a0ac54266c9d9dd75e933127...   
22544     2020-01-02  37e81d3b920643244cf8b0ffdc412c0268e9fca6e8e007...   
22734     2020-01-02  38ccf571c08f754a346bbf62a36dfa51b235134b6a82b8...   
22850     2020-01-02  39649fc9237c15aa38310048e50e417fa95719ffac964e...   
23171     2020-01-02  3babbb802c51c6f82a4a838c1a8161939c2ff820353d95...   
23172     2020-01-02  3babbb802c51c6f82a4a838c1a8161939c2ff820353d95...   
23304     2020-01-02  3ce11464cc0ef013767dcfffa98f0a2488620b22a04d95...   
23807     2020-01-02  3f76aa1d541a73114dda4c6ea44811bdda756bb00aa043...   
24578     2020-01-02  441642b2982f97f539b8552c14de19a1504c8709225ea7...   
24597     2020-01-02  44299849e81273ffaefbd259c5236725eb6257797e7332...   
24765     2020-01-02  45524ffae5ff84e9b3e9476b8aa0eeac06a70041dc4682...   
26185     2020-01-02  4cc971ab11c04a9229a2910e228269fe0e2f6096314ae0...   
26203     2020-01-02  4cf4e491c0ea89b818dacc685dca3de91ade69d1bca8ae...   
26216     2020-01-02  4cfda73b0977688c8218a11716e31c64f3ff620c7f2964...   
26225     2020-01-02  4d103cd1684be59ff5a66cba294b804667de6d80d5e78b...   
26309     2020-01-02  4d58e85de14dff89c4486b27805fe78cf5974198f04875...   
26670     2020-01-02  5006aba6395afa4f2f024a269681f007db0f43f565e92b...   
26671     2020-01-02  5006aba6395afa4f2f024a269681f007db0f43f565e92b...   
27362     2020-01-02  549598ac0bca2d94cc0ff97cb068a32a91dc122d687970...   
28294     2020-01-02  5a16699699d27b4ff39b309fc041c3dec5db53563bab89...   
28923     2020-01-02  5e12cba42a517629c59f6a97a24bd6b13ff628f3dc1fcd...   
29860     2020-01-02  63bfa3208d24a155190988f8d2606a4ab0226347014412...   
30142     2020-01-02  65d77d6749ca401b13b1b6db534ac9d6f294ed132472cb...   
31384     2020-01-02  6d52521b6aad385d0a5a01150eae1f4cea57ddc4350f52...   
33221     2020-01-02  77c1f11562ba4e992e04d4c91297bcccaf5931cace92ae...   
33858     2020-01-02  7adfd683b3358afb6fe5a9640bd378507fd6b2e9c8039a...   
34435     2020-01-02  7e3984aaadb336ced0

In [11]:
HMRecommendationDF.dropna(subset=['product_code', 'prod_name', 'product_type_no', 'department_no', 'department_name','detail_desc' ], inplace=True)

#HMRecommendationDF = HMRecommendationDF[HMRecommendationDF['product_code', 'prod_name', 'product_type_no', 'department_no', 'department_name','detail_desc'].notna()]

In [12]:
HMRecommendationDF.head(3)

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   
2  2018-09-20  00007d2de826758b65a93dd24ce629ed66842531df6699...   505221004   

      price  Active   age  product_code                 prod_name  \
0  0.050831     NaN  24.0        663713  Atlanta Push Body Harlow   
1  0.030492     NaN  24.0        541518   Rae Push (Melbourne) 2p   
2  0.015237     1.0  32.0        505221               Inca Jumper   

   product_type_no  department_no      department_name  \
0              283           1338  Expressive Lingerie   
1              306           1334      Casual Lingerie   
2              252           5963     Tops Knitwear DS   

                                         detail_desc  
0  Lace push-up body with underwired, moulded, pa...  
1  Lace push-up bras with underwired, moulded, pa...  
2  Jumper in rib-knit cotton with hard-worn detai...

In [14]:
#HMRecommendationDF = HMRecommendationDF.drop(['FN', 'club_member_status', 'fashion_news_frequency', 'postal_code'], axis=1)

In [13]:
listBin = [-1, 19, 29, 39, 49, 59, 69, 119]
HMRecommendationDF['age_bins'] = pd.cut(HMRecommendationDF['age'], listBin)

In [16]:
HMRecommendationDF.head(2)

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   

      price  sales_channel_id  Active   age  product_code  \
0  0.050831                 2     NaN  24.0      663713.0   
1  0.030492                 2     NaN  24.0      541518.0   

                  prod_name  product_type_no  department_no  \
0  Atlanta Push Body Harlow            283.0         1338.0   
1   Rae Push (Melbourne) 2p            306.0         1334.0   

       department_name                                        detail_desc  \
0  Expressive Lingerie  Lace push-up body with underwired, moulded, pa...   
1      Casual Lingerie  Lace push-up bras with underwired, moulded, pa...   

   age_bins  
0  (19, 29]  
1  (19, 29]

In [18]:
HMRecommendationDF['Active'].value_counts()

1.0    13328528
Name: Active, dtype: int64

In [14]:
HMRecommendationDF['Active'] = HMRecommendationDF['Active'].fillna(0)

In [20]:
HMRecommendationDF.head(2)

t_dat                                        customer_id  article_id  \
0  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   663713001   
1  2018-09-20  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   541518023   

      price  sales_channel_id  Active   age  product_code  \
0  0.050831                 2     0.0  24.0      663713.0   
1  0.030492                 2     0.0  24.0      541518.0   

                  prod_name  product_type_no  department_no  \
0  Atlanta Push Body Harlow            283.0         1338.0   
1   Rae Push (Melbourne) 2p            306.0         1334.0   

       department_name                                        detail_desc  \
0  Expressive Lingerie  Lace push-up body with underwired, moulded, pa...   
1      Casual Lingerie  Lace push-up bras with underwired, moulded, pa...   

   age_bins  
0  (19, 29]  
1  (19, 29]

In [21]:
HMRecommendationDF.shape

(31673297, 14)

In [15]:
HMRecommendationDF = HMRecommendationDF.sample(n=1000000)

In [16]:
HMRecommendationDF.shape

(1000000, 13)

In [17]:
HMRecommendationDF.to_csv('HMRecommendation.csv')

In [18]:
HMRecommendationDF.isna().sum()

t_dat                 0
customer_id           0
article_id            0
price                 0
Active                0
age                4382
product_code          0
prod_name             0
product_type_no       0
department_no         0
department_name       0
detail_desc           0
age_bins           4382
dtype: int64

In [19]:
HMRecommendationDF = HMRecommendationDF.drop(['age_bins'], axis=1)

In [20]:
HMRecommendationDF.isna().sum()

t_dat                 0
customer_id           0
article_id            0
price                 0
Active                0
age                4382
product_code          0
prod_name             0
product_type_no       0
department_no         0
department_name       0
detail_desc           0
dtype: int64

In [24]:
HMRecommendationDF['age']=HMRecommendationDF['age'].fillna(HMRecommendationDF['age'].mean())

In [25]:
HMRecommendationDF.isna().sum()

t_dat              0
customer_id        0
article_id         0
price              0
Active             0
age                0
product_code       0
prod_name          0
product_type_no    0
department_no      0
department_name    0
detail_desc        0
dtype: int64

In [26]:
# impute the age column
listBin = [-1, 19, 29, 39, 49, 59, 69, 119]
HMRecommendationDF['age_bins'] = pd.cut(HMRecommendationDF['age'], listBin)

In [27]:
HMRecommendationDF.shape

(1000000, 13)

In [28]:
HMRecommendationDF.to_csv('HMRecommendation.csv')

In [29]:
HMRecommendationDF.head()

t_dat                                        customer_id  \
6922705   2019-03-03  5d65859e7099a62c882a650d8b49f4bcc710c86dceac78...   
21666620  2020-01-26  108677d03acde3012a2f843e1a6b3063ff5ab61ef9b2b7...   
5153074   2019-01-18  f881cfb571c1948d48931025ffdad9749159c49642ec6d...   
22819250  2020-02-28  39180e9299631c46cebf0940c5b6dfc5c62195bc2e5ad9...   
666428    2018-10-02  d2148c51fc1094b6d9755356c704f531b6681b4c82bb24...   

          article_id     price  Active   age  product_code  \
6922705    709996003  0.033881     0.0  33.0        709996   
21666620   624257028  0.084729     0.0  30.0        624257   
5153074    624636002  0.008458     1.0  34.0        624636   
22819250   658030029  0.050831     1.0  30.0        658030   
666428     477107015  0.016932     0.0  52.0        477107   

                           prod_name  product_type_no  department_no  \
6922705                     Cilantro              265           1313   
21666620   &DENIM+ Skinny shaping RW              272           1774   
5153074                       Jessie               80           3409   
22819250         Push Up Jegging L.W              272           1772   
666428    Ellen Bikini Clover Mid 3p              286           1334   

            department_name  \
6922705               Dress   
21666620  OL Extended Sizes   
5153074             Scarves   
22819250     Denim Trousers   
666428      Casual Lingerie   

                                                detail_desc  age_bins  
6922705   Short dress in woven fabric with a round neckl...  (29, 39]  
21666620  Shaping. 5-pocket jeans in washed denim with t...  (29, 39]  
5153074   Large, block-coloured scarf in a soft weave wi...  (29, 39]  
22819250  5-pocket jeggings in washed, stretch denim wit...  (29, 39]  
666428    Bikini briefs in organic cotton jersey with a ...  (49, 59]

In [30]:
HMRecommendationDF.dtypes

t_dat                object
customer_id          object
article_id            int64
price               float64
Active              float64
age                 float64
product_code          int64
prod_name            object
product_type_no       int64
department_no         int64
department_name      object
detail_desc          object
age_bins           category
dtype: object

In [31]:
HMRecommendationDF['t_dat'] = pd.to_datetime(HMRecommendationDF['t_dat'])

In [32]:
HMRecommendationDF.dtypes

t_dat              datetime64[ns]
customer_id                object
article_id                  int64
price                     float64
Active                    float64
age                       float64
product_code                int64
prod_name                  object
product_type_no             int64
department_no               int64
department_name            object
detail_desc                object
age_bins                 category
dtype: object

### Model

In [38]:
# For improvments refer to https://www.tensorflow.org/recommenders
import tensorflow_recommenders as tfrs

from pathlib import Path
from typing import Dict, Text

In [49]:
unique_customer_ids = HMRecommendationDF['customer_id'].unique()
unique_article_ids = HMRecommendationDF['article_id'].unique() 

article_ds = tf.data.Dataset.from_tensor_slices(dict(HMRecommendationDF[['article_id']]))
articles = article_ds.map(lambda x: x['article_id'])

In [40]:
embedding_dimension = 64

# Customer ID
customer_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_customer_ids, mask_token=None),  
  tf.keras.layers.Embedding(len(unique_customer_ids) + 1, embedding_dimension)
])

In [42]:
HMRecommendationDF['article_id'] = HMRecommendationDF['article_id'].astype(str)

In [45]:
# Article ID
article_model = tf.keras.Sequential([
  tf.keras.layers.StringLookup(
      vocabulary=unique_article_ids, mask_token=None),
  tf.keras.layers.Embedding(len(unique_article_ids) + 1, embedding_dimension)
])

In [46]:
class HMRModel(tfrs.Model):
    
    def __init__(self, customer_model, article_model):
        super().__init__()
        self.article_model: tf.keras.Model = article_model
        self.customer_model: tf.keras.Model = customer_model
        self.task = tfrs.tasks.Retrieval(
        metrics=tfrs.metrics.FactorizedTopK(
            candidates=articles.batch(128).map(self.article_model),            
            ),
        )        

    def compute_loss(self, features: Dict[str, tf.Tensor], training=False) -> tf.Tensor:
    
        customer_embeddings = self.customer_model(features["customer_id"])    
        article_embeddings = self.article_model(features["article_id"])

        # Returns loss and the metrics of the model 
        return self.task(customer_embeddings, article_embeddings,compute_metrics=not training)


### Training and Validating the Model

In [50]:
model = HMRModel(customer_model, article_model)
model.compile(optimizer=tf.keras.optimizers.Adagrad(learning_rate=0.1))

In [51]:
# Splittng the data
HMRecommendationDF['t_dat'].max() , HMRecommendationDF['t_dat'].min()

(Timestamp('2020-09-22 00:00:00'), Timestamp('2018-09-20 00:00:00'))

In [52]:
from sklearn.model_selection import train_test_split

In [54]:
# 70% training and 30% Testing
train_temp=HMRecommendationDF.sample(frac=0.7,random_state=200) 
test_temp=HMRecommendationDF.drop(train_temp.index)

In [55]:
train_temp.shape, test_temp.shape

((700000, 13), (300000, 13))

In [56]:
train_data = tf.data.Dataset.from_tensor_slices(dict(train_temp[['customer_id','article_id']])).shuffle(100_000).batch(256).cache()
test_data = tf.data.Dataset.from_tensor_slices(dict(test_temp[['customer_id','article_id']])).batch(256).cache()

num_epochs = 5

In [57]:
history = model.fit(train_data, epochs=num_epochs, verbose=1)

Epoch 1/5
2735/2735 [==============================] - 18s 6ms/step - factorized_top_k/top_1_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_5_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_10_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_50_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_100_categorical_accuracy: 0.0000e+00 - loss: 1418.7702 - regularization_loss: 0.0000e+00 - total_loss: 1418.7702
Epoch 2/5
2735/2735 [==============================] - 11s 4ms/step - factorized_top_k/top_1_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_5_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_10_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_50_categorical_accuracy: 0.0000e+00 - factorized_top_k/top_100_categorical_accuracy: 0.0000e+00 - loss: 1373.4536 - regularization_loss: 0.0000e+00 - total_loss: 1373.4536
Epoch 3/5
2735/2735 [==============================] - 11s 4ms/step - factorized_top_k/top_1_categorical_accuracy: 0.0000e+0